# Objective:

This notebook consists of 2 sections to demonstrate [row-level security (RLS) enhancements in Amazon Redshift that were announced at re:invent 2023](https://aws.amazon.com/about-aws/whats-new/2023/11/amazon-redshift-row-level-security-enhancements/). 

## Section 1) Applying RLS on standard views and late binding views
## Section 2) Using CONJUNCTION TYPE for row-level security (RLS) policies

By the end of this demo, you will know how to apply granular access controls and ensure that users can only access rows that they are authorized to see, even when the underlying data evolves or user permissions change.

# Pre-requisites

1. [Create Redshift Serverless workgroup](https://docs.aws.amazon.com/redshift/latest/mgmt/serverless-console-workgroups-create-workgroup-wizard.html) and [open the Redshift Query Editor v2](https://docs.aws.amazon.com/redshift/latest/mgmt/query-editor-v2-using.html#query-editor-v2-open).  
2. Ensure you [setup an IAM role as default IAM role](https://docs.aws.amazon.com/redshift/latest/mgmt/default-iam-role.html#managing-iam-role-console). 
3. Load sample dataset TICKIT which is located in the sample_data_dev. On the left side of Redshift Query Editor, click: *Serverless: your_workgroup_name* -> *sample_data_dev* -> *tickit*. TICKIT dataset consists of sales activity for the fictional TICKIT web site, where users buy and sell tickets online for sporting events, shows, and concerts. 
4. Change your connection to the database *sample_data_dev* using the dropdown menu at the top of the notebook page.

*Tip*: Redshift has many system tables and views that contain information about how the system is functioning. During the workshop, you could query system views such as [SVV_RLS_ATTACHED_POLICY](https://docs.aws.amazon.com/redshift/latest/dg/r_SVV_RLS_ATTACHED_POLICY.html), [SVV_RLS_POLICY](https://docs.aws.amazon.com/redshift/latest/dg/r_SVV_RLS_POLICY.html) and [SVV_RLS_RELATION](https://docs.aws.amazon.com/redshift/latest/dg/r_SVV_RLS_RELATION.html) for RLS related changes that had taken affect.

# Section 1: Applying RLS on standard views and late binding views

1. As first step, confirm that you have access to the table *users* by displaying the table entries using SELECT statement.

In [0]:
SELECT * FROM "sample_data_dev"."tickit"."users" LIMIT 10;

2. Create a standard view and late binding view based on *users* table with only the columns that store personal data.

In [0]:
-- Create standard view
CREATE VIEW PersonalData AS
    SELECT
        firstname,
        lastname,
        city,
        state,
        email,
        phone
    FROM
        "tickit"."users";

-- Create late binding view
CREATE VIEW PersonalData_LBV AS
    SELECT
        firstname,
        lastname,
        city,
        state,
        email,
        phone
    FROM
        "tickit"."users"
WITH NO SCHEMA BINDING;

3. Take a look at the entries in *PersonalData* view using SELECT. You can see that this view contains entries covering various US states.

In [0]:
SELECT * FROM PersonalData LIMIT 10;

4. A new officer Jane had started working at the Nevada office. Create a new role for her, grant SELECT access to her for personal data views and protect sensitive data by limiting her access to users who live in Nevada state.

In [0]:
-- Create an Nevada (NV) analyst role and grant it to a user named Jane.
CREATE ROLE NVanalyst;
CREATE USER Jane WITH PASSWORD 'Name_is_Jane_1';
GRANT SELECT ON PersonalData TO ROLE NVanalyst;
GRANT SELECT ON PersonalData_LBV TO ROLE NVanalyst;
GRANT ROLE NVanalyst TO Jane;

-- Create an RLS policy that only lets the user see users in Nevada.
CREATE RLS POLICY policyNV
WITH (state CHARACTER(2))
USING (state = 'NV');

-- Attach RLS policy to the Nevada (NV) analyst role on both views.
ATTACH RLS POLICY policyNV ON PersonalData TO ROLE NVanalyst;
ATTACH RLS POLICY policyNV ON PersonalData_LBV TO ROLE NVanalyst;

-- Activate RLS on the views. 
ALTER TABLE PersonalData ROW LEVEL SECURITY ON;
ALTER TABLE PersonalData_LBV ROW LEVEL SECURITY ON;

5. Change the session user to Jane and test if her views are limited by the new policy.

In [0]:
SET SESSION AUTHORIZATION Jane;

SELECT * FROM PersonalData LIMIT 10;

SELECT * FROM PersonalData_LBV LIMIT 10;

Success! You have completed the first section of this demo. Before continuing with the second section, set your session user back to default to have necessary superuser permissions.

In [0]:
SET SESSION AUTHORIZATION DEFAULT;

# Section 2: CONJUNCTION TYPE support for row-level security (RLS) policies

1. Confirm that you have access to the table *category* by displaying the table entries using SELECT statement.

In [0]:
SELECT * FROM "sample_data_dev"."tickit"."category" LIMIT 10;

2. Analyst Joe had recently joined to the business. He needs to only see categories in Sports category group (catgroup) and categories with the category name (catname) of NBA. 

    Create a new role for Joe, associate new RLS policies with his role and activate RLS on the category table with AND CONJUNCTION TYPE.

In [0]:
-- Create an analyst role and grant it to a user named Joe.
CREATE ROLE analyst;
CREATE USER Joe WITH PASSWORD 'Name_is_joe_1';
GRANT ROLE analyst TO Joe;

-- Create an RLS policy that only lets the user see sports.
CREATE RLS POLICY policy_sports
WITH (catgroup VARCHAR(10))
USING (catgroup = 'Sports');

-- Create an RLS policy that only lets the user see NBA.
CREATE RLS POLICY policy_nba
WITH (catname VARCHAR(10))
USING (catname = 'NBA');

-- Attach both to the analyst role.
ATTACH RLS POLICY policy_sports ON "sample_data_dev"."tickit"."category" TO ROLE analyst;
ATTACH RLS POLICY policy_nba ON "sample_data_dev"."tickit"."category" TO ROLE analyst;

-- Activate RLS on the category table with AND CONJUNCTION TYPE. 
ALTER TABLE "sample_data_dev"."tickit"."category" ROW LEVEL SECURITY ON CONJUNCTION TYPE AND;

3. Change the session user to Joe and test if his access in table is limited by the new policies. If your RLS policies had taken affect successfuly, Joe can only view 1 category with catname=NBA in catgroup=Sports.

In [0]:
-- Change session to Joe.
SET SESSION AUTHORIZATION Joe;

-- Select all from the category table.
SELECT catgroup, catname
FROM "sample_data_dev"."tickit"."category";

4. When the multiple policies should permit the users to see more rows in a given relation, you could use RLS CONJUNCTION TYPE of the relation to OR. Change Joe's permissions to let him see "Concerts" and "Sports".

In [0]:
-- Change session authorization to default to have permissions to create RLS policies.
SET SESSION AUTHORIZATION DEFAULT;

-- Create an RLS policy that only lets the user see concerts.
CREATE RLS POLICY policy_concerts
WITH (catgroup VARCHAR(10))
USING (catgroup = 'Concerts');

-- Attach new policy to the analyst role. Now analyst role will have 3 policies attached.
ATTACH RLS POLICY policy_concerts ON "sample_data_dev"."tickit"."category" TO ROLE analyst;

-- Activate RLS on the category table with OR CONJUNCTION TYPE.
-- With this command, all 3 policies will be connected with an OR statement.
ALTER TABLE "sample_data_dev"."tickit"."category" ROW LEVEL SECURITY ON CONJUNCTION TYPE OR;

4. Change the session user to Joe and test if his access in table has changed. If your RLS policies had taken affect successfuly, Joe can view 8 categories now!

In [0]:
-- Change session to Joe.
SET SESSION AUTHORIZATION Joe;

SELECT catgroup, catname
FROM "sample_data_dev"."tickit"."category";

5. Congrats! You had succesfully finished this workshop. If you set up a Redshift Serverless workgroup to complete this exercise, when you are finished with the exercise, delete the workgroup. Deleting it stops accruing charges to your AWS account. To delete the workgroup, follow the steps in [Deleting a workgroup](https://docs.aws.amazon.com/redshift/latest/mgmt/serverless_delete-workgroup.html) in the Amazon Redshift Management Guide.